In [1]:
import sys
import numpy as np
import pandas as pd
import pickle
import re
import math
import os
os.environ['KMP_DUPLICATE_LIB_OK']='True'
sys.path.append(os.path.join(os.path.abspath(os.getcwd()),".."))
sys.path.append(os.path.join(os.path.abspath(os.getcwd()),"../.."))
parent_dir = os.path.abspath(os.path.join(os.getcwd(), '../..'))

In [4]:
# import MEIRL Modules
from maxent_irl.maxent_irl_utils import *
#from maxent_irl.Reward_Expert import *
from maxent_irl.maxent_irl import *
from utils.trajectory import Trajectory
from utils.plot_utils import *

In [5]:
# Settings for the different cases
feat_list_cases = [["laptop", "coffee", "table"],["laptop", "coffee", "table"], ["proxemics", "coffee", "table"]]
weights_cases = [[10.0, 0.0, 10.0], [10.0, 0.0, 10.0], [10.0, 0.0, 10.0]]
known_features_cases = [["table", "coffee"], ["laptop", "coffee"], ["table", "coffee"]]

traj_feat_list = [ "tablelaptop_case1", "tablelaptop_case2", "tableproxemics_case3"]
traj_idx_list = [[4, 13,0, 15], [0,1,2,3,4,5,6,7], [1,2,3,4,6]]


# TrajOpt Settings
obj_center_dict = {'HUMAN_CENTER': [-0.2, -0.5, 0.6], 'LAPTOP_CENTER': [-0.6, 0.0, 0.0]}
T = 20.0
timestep=0.5

In [6]:
# Settings for the different cases
feat_list_cases = [[]]
weights_cases = [[]]
known_features_cases = [[]]

traj_feat_list = []
traj_idx_list = [[0,1,2,3,4]]


# TrajOpt Settings
obj_center_dict = {'HUMAN_CENTER': [-0.2, -0.5, 0.6], 'LAPTOP_CENTER': [-0.6, 0.0, 0.0]}
T = 20.0
timestep=0.5

# 1. Load or Generate near-optimal expert demonstrations

In [7]:
# Setting for which Case (see paper)
case = 1

# adjust accordingly
feat_list = feat_list_cases[case-1]
weights = weights_cases[case-1]
known_features = known_features_cases[case-1]

## 1.1 Load human expert demonstrations

In [9]:
parent_dir

'/root/catkin_ws/src/jaco_learning'

In [10]:
# CHANGED
trajectory_list = [np.load(parent_dir + '/../jaco_learning/data/pour_red{}.npy'.format(i)) for i in range(5)]

# ORIGINAL
# # load in a set of demonstrations
# data_file = parent_dir + '/data/MEIRL_demonstrations/demos_{}.p'.format(traj_feat_list[case-1])
# trajectory_list = pickle.load(open( data_file, "rb" ) )

# select subset of demonstrations & sample to fit T, timestep setting of trajopt
s_g_exp_trajs = []
for i, trajectory in enumerate(trajectory_list):
    if i not in traj_idx_list[case-1]:
        continue
    waypts = trajectory
    waypts_time = np.linspace(0.0, T, waypts.shape[0])
    traj = Trajectory(waypts, waypts_time)

    # Downsample/Upsample trajectory to fit desired timestep and T.
    num_waypts = int(T / timestep) + 1
    if num_waypts < len(traj.waypts):
        demo = traj.downsample(int(T / timestep) + 1)
    else:
        demo = traj.upsample(int(T / timestep) + 1)
    s_g_exp_trajs.append([demo.waypts])

## 1.2 generate near-optimal expert demonstrations

In [11]:
# extract start & goal positions from the respective demonstrations
# starts = []
# goals = []
# for trajectory in [trajectory_list[i] for i in traj_idx_list[case-1]]:
#     starts.append(trajectory[0])
#     goals.append(trajectory[-1])
    
starts = []
goals = []
for trajectory in [trajectory_list[i] for i in traj_idx_list[case-1]]:
    starts.append(trajectory[0])
    goals.append(trajectory[-1])

# Environment setup

In [15]:
parent_dir

'/root/catkin_ws/src/jaco_learning'

In [17]:
import yaml
with open(parent_dir + '/config/teleop_inference.yaml') as f:
    config = yaml.load(f)

In [18]:
config

{'controller': {'d_gain': 0.1,
  'epsilon': 0.1,
  'i_gain': 0.1,
  'max_cmd': 40.0,
  'p_gain': 0.8,
  'type': 'pid'},
 'learner': {'assistance_method': 'blend',
  'beta_method': 'estimate',
  'beta_priors': [-10000, 2, 2],
  'betas': [0.1, 1, 10.0],
  'goal_beliefs': [1.0, 0.0, 0.0],
  'inference_method': 'dragan',
  'zero_input_assist': True},
 'planner': {'max_iter': 50, 'num_waypts': 5, 'type': 'trajopt'},
 'setup': {'T': 20.0,
  'common_feat_list': ['efficiency'],
  'common_feat_weights': [1.0],
  'goal_dist_feat_weight': 0.0,
  'goals': [[150.0, 130.0, 160.0, 240.0, 180.0, 172.0, 280.0],
   [210.0, 130.0, 200.0, 240.0, 180.0, 172.0, 280.0]],
  'model_filename': 'jaco_dynamics',
  'object_centers': {'HUMAN_CENTER': [-0.6, -0.55, 0.0],
   'LAPTOP_CENTER': [-0.7929, -0.1, 0.0]},
  'prefix': 'j2s7s300_driver',
  'save_dir': '/data/teleoperation/',
  'start': [180.0, 150.0, 180.0, 270.0, 180.0, 180.0, 190.0],
  'timestep': 0.5}}

In [24]:
# simulate a TeleopInference object
class Main():
    def __init__(self):
        pass
main = Main()

In [ ]:
main.prefix = config["setup"]["prefix"]
main.T = rospy.get_param("setup/T")
main.timestep = rospy.get_param("setup/timestep")
main.save_dir = rospy.get_param("setup/save_dir")

main.start = np.array(rospy.get_param("setup/start"))*(math.pi/180.0)
main.start += np.random.normal(0, 0.157, self.start.shape)

# ----- Goals and goal weights setup ----- #
# TODO: remove one of these
#self.goal_poses = np.array(rospy.get_param("setup/goal_poses"))
fixed_goals = [np.array(goal)*(math.pi/180.0) for goal in rospy.get_param("setup/goals")]
try:
    learned_goals = np.load('learned_goals.npy')
    main.goals = fixed_goals + learned_goals
except IOError:
    main.goals = fixed_goals

main.feat_list = rospy.get_param("setup/common_feat_list")
feat_range = {'table': 0.98,
              'coffee': 1.0,
              'laptop': 0.3,
              'human': 0.3,
              'efficiency': 0.22,
              'proxemics': 0.3,
              'betweenobjects': 0.2}
common_weights = rospy.get_param("setup/common_feat_weights")
goals_weights = []
goal_dist_feat_weight = rospy.get_param("setup/goal_dist_feat_weight")
if goal_dist_feat_weight != 0.0:
    # add features for distance from each of the goals
    common_weights = common_weights + ([0.] * len(self.goals))
    num_feats = len(main.feat_list)
    for goal_num in range(len(self.goals)):
        main.feat_list.append("goal"+str(goal_num)+"_dist")
        goal_weights = np.array(common_weights)
        goal_weights[num_feats + goal_num] = goal_dist_feat_weight
        goals_weights.append(goal_weights)
else:
    # make copies of the common weights
    for goal_num in range(len(main.goals)):
        goals_weights.append(np.array(common_weights))
main.goal_weights = goals_weights

# Openrave parameters for the environment.
model_filename = rospy.get_param("setup/model_filename")
object_centers = rospy.get_param("setup/object_centers")
main.environment = Environment(model_filename,
                               object_centers,
                               main.feat_list,
                               feat_range,
                               goals=main.goals,
                               use_viewer=False,
                               plot_objects=False)
main.goal_locs = main.environment.goal_locs

# ----- Planner Setup ----- #
# Retrieve the planner specific parameters.
planner_type = rospy.get_param("planner/type")
if planner_type == "trajopt":
    max_iter = rospy.get_param("planner/max_iter")
    num_waypts = rospy.get_param("planner/num_waypts")

    # Initialize planner and compute trajectory to track.
    main.planner = TrajoptPlanner(max_iter, num_waypts, self.environment)
else:
    raise Exception('Planner {} not implemented.'.format(planner_type))

# Save a history of waypts
main.next_waypt_idx = 1
main.traj_hist = np.zeros((int(main.T/main.timestep) + 1, 7))
main.traj_hist[0] = self.start

# ----- Add in learned cost function goals -----
# 1. create new weight vectors
common_weights = common_weights + [0]
for i in range(len(main.goal_weights)):
    main.goal_weights[i] = np.hstack((main.goal_weights[i], 0))
learned_goal_weight = np.array(common_weights)
learned_goal_weight[len(self.feat_list)] = 1.
self.goal_weights.append(learned_goal_weight)

# this reuses the first goal for the learned feature
# 2. add cost to environment
meirl_goal_save_path = "/root/catkin_ws/src/jaco_learning/data/pour_red_meirl.pt"
self.environment.load_meirl_learned_feature(self.planner, learned_goal_weight, self.goals[0], meirl_goal_save_path)

# ----- Controller Setup ----- #
# Retrieve controller specific parameters.
controller_type = rospy.get_param("controller/type")
if controller_type == "pid":
    # P, I, D gains.
    P = rospy.get_param("controller/p_gain") * np.eye(7)
    I = rospy.get_param("controller/i_gain") * np.eye(7)
    D = rospy.get_param("controller/d_gain") * np.eye(7)

    # Stores proximity threshold.
    epsilon = rospy.get_param("controller/epsilon")

    # Stores maximum COMMANDED joint torques.
    MAX_CMD = rospy.get_param("controller/max_cmd") * np.eye(7)

    self.controller = PIDController(P, I, D, epsilon, MAX_CMD, self)
else:
    raise Exception('Controller {} not implemented.'.format(controller_type))

# Planner tells controller what plan to follow.
self.controller.set_trajectory(self.traj)

# Stores current COMMANDED joint velocities.
self.cmd = np.zeros((7,7))

# ----- Learner Setup ----- #
betas = np.array(rospy.get_param("learner/betas"))
goal_beliefs = rospy.get_param("learner/goal_beliefs")
if goal_beliefs != "none":
    goal_beliefs = goal_beliefs / np.linalg.norm(goal_beliefs)
else:
    goal_beliefs = np.ones(len(self.goals))/len(self.goals)
assert(len(goal_beliefs) == len(self.goals))
assert(len(goal_beliefs) == len(self.goal_weights))
beta_priors = rospy.get_param("learner/beta_priors")
inference_method = rospy.get_param("learner/inference_method")
self.beta_method = rospy.get_param("learner/beta_method")
self.learner = TeleopLearner(self, goal_beliefs, beta_priors, betas, inference_method, self.beta_method)
self.running_inference = False
self.last_inf_idx = 0
self.running_final_inference = False
self.final_inference_done = False

# ----- Input Device Setup ----- #
self.joy_environment = Environment(model_filename,
                                   object_centers,
                                   list(), # doesn't need to know about features
                                   dict(),
                                   #goals=self.goals,
                                   use_viewer=False,
                                   plot_objects=False)
self.joy_cmd = np.zeros((7,7))
self.assistance_method = rospy.get_param("learner/assistance_method")
self.alpha = 1. # in [0, 1]; higher numbers give more control to human
self.zero_input_assist = rospy.get_param("learner/zero_input_assist")

# IRL

In [13]:
NN_dict = {'n_layers': 2, 'n_units':128,
           'sin':False, 'cos':False, 'noangles':True, 'norot':False,
           'rpy':False, 'lowdim':True, 'noxyz':True, 'EErot':True,
           '6D_laptop':False, '6D_human':False, '9D_coffee':False}

IRL_dict = {'n_iters': 50,
            'n_cur_rew_traj': 1,
            'lr':1e-3, 'weight_decay':0.001, 'std':0.01}

IRL = DeepMaxEntIRL(s_g_exp_trajs=s_g_exp_trajs,
                    goal_poses=None,
                    known_feat_list=known_features,
                    NN_dict=NN_dict,
                    gen='waypt')

TypeError: __init__() takes at least 9 arguments (6 given)

In [16]:
# Before IRL: Compare the demonstration trajectories & the current cost induced trajectories
# Colors are the randomly initialized Neural Network cost function
plot_IRL_comparison(IRL, [61,64,67], 6)
#plot_IRL_comparison(IRL, frame_idx=6)

In [17]:
plot_IRL_comparison(IRL, frame_idx=6)

In [18]:
IRL.deep_max_ent_irl(n_iters=IRL_dict['n_iters'], n_cur_rew_traj=IRL_dict['n_cur_rew_traj'],
                     lr=IRL_dict['lr'], weight_decay=IRL_dict['weight_decay'], std=IRL_dict['std'])

Iteration 49: 100%|██████████| 50/50 [01:42<00:00,  2.05s/it, avg_loss=0]      


In [19]:
# After IRL: Compare the demonstration trajectories & the current cost induced trajectories
# Colors are the learned Neural Network cost function
plot_IRL_comparison(IRL, [61,64,67], 6)

# Visualize the learned cost function in 3D 

In [20]:
# plot GT
plot_gt3D(parent_dir, Expert.env)

ValueError: All arguments should have the same length. The length of argument `color` is 1, whereas the length of  previously-processed arguments ['x', 'y', 'z'] is 7656

In [21]:
# plot learned
plot_learned3D(parent_dir, IRL.function, IRL.env)

In [32]:
def save(self):
    torch.save({
        "known_feat_list": self.known_feat_list,
        "s_g_exp_trajs": Expert.return_trajs(),
        "goal_poses": self.goal_poses,
        "NN_dict": self.NN_dict,
        "gen": self.gen,
        "cost_nn_state_dict": self.cost_nn.state_dict(),
        "max_label": self.max_label,
        "min_label": self.min_label
    }, "/root/catkin_ws/src/jaco_learning/data/pour_red_meirl.pt")

In [33]:
save(IRL)

In [26]:
'test' in 'test1'

True

In [27]:
np.zeros(1)

array([0.])

In [29]:
np.hstack((np.arange(5), 5))

array([0, 1, 2, 3, 4, 5])

In [34]:
np.arange(5)[np.arange(5) > 3]

array([4])